# Summary of AGIPD dark characterization #


In [ ]:
cluster_profile = "noDB" # The ipcluster profile to use
out_folder = "/gpfs/exfel/data/scratch/ahmedk/test/SPB/DARK/AGIPD3/" # path to output to, required
dinstance = "AGIPD1M1"

In [ ]:
from collections import OrderedDict
import copy
from datetime import datetime
import os
import warnings
warnings.filterwarnings('ignore')

import glob
import h5py
from IPython.display import display, Markdown, Latex
import numpy as np
import matplotlib
matplotlib.use("agg")
import matplotlib.patches as patches
import matplotlib.pyplot as plt
%matplotlib inline
import tabulate
from cal_tools.ana_tools import get_range
from extra_geom import AGIPD_1MGeometry
from iCalibrationDB import Detectors
from XFELDetAna.plotting.heatmap import heatmapPlot
from XFELDetAna.plotting.simpleplot import simplePlot

In [ ]:
# TODO: After changes in the Cal DB interface read files from cal repository

# Load constants from local files
data = OrderedDict()
old_cons = OrderedDict()
mod_names = []
# Loop over modules
for i in range(16):
    qm = "Q{}M{}".format(i//4 + 1, i % 4 + 1)
    # loop over constants
    detinst = getattr(Detectors, dinstance)
    for const in ['Offset', 'Noise', 'ThresholdsDark', 'BadPixelsDark']:
        det = getattr(detinst, qm)
        if det is None:
            continue
        det_name = det.device_name

        fpath = '{}/const_{}_{}.h5'.format(out_folder, const, det_name)
        oldfpath = '{}/old/const_{}_{}.h5'.format(out_folder, const, det_name)
        if not os.path.isfile(fpath):
            continue
        with h5py.File(fpath, 'r') as f:
            if qm not in data:
                mod_names.append(qm)
                data[qm] = OrderedDict()

            data[qm][const] = f["data"][()]

        if not os.path.isfile(oldfpath):
            continue

        with h5py.File(oldfpath, 'r') as oldf:
            if qm not in old_cons:
                old_cons[qm] = OrderedDict()
            old_cons[qm][const] = oldf["data"][()]


In [ ]:
modules = np.argsort(mod_names)
cons_shape = {}
# extracting constant shape.
for qm, constant in data.items():
    for cname, cons in constant.items():
        shape = data[qm][cname].shape
        if cname not in cons_shape:
            cons_shape[cname] = shape
    break
constants = {}
prev_const = {}
for cname, sh in cons_shape.items():
    constants[cname]= np.zeros((len(mod_names),) + sh[:])
    prev_const[cname]= np.zeros((len(mod_names),) + sh[:])
for i, mod in enumerate(modules):
    for cname, cval in constants.items():
        # move 3 gain maps from last indices to first three
        if cname == 'ThresholdsDark':
            cval[i][..., :3] = data[mod_names[mod]][cname][...,2:]
            cval[i][..., 3:] = data[mod_names[mod]][cname][...,:2]
        else:
            cval[i] = data[mod_names[mod]][cname]

    for cname, cval in prev_const.items():
        if cname == 'ThresholdsDark':
            cval[i][..., :3] = old_cons[mod_names[mod]][cname][..., 2:]
            cval[i][..., 3:] = old_cons[mod_names[mod]][cname][..., :2]
        else:
            cval[i] = old_cons[mod_names[mod]][cname]
mod_names = np.array(mod_names)[modules]

In [ ]:
display(Markdown('## Processed modules ##'))

fig, ax = plt.subplots(1, figsize=(10, 10))
ax.set_axis_off()

ax.set_xlim(0, 90)
ax.set_ylim(0, 75)
asic_pos = 5

q_st = 8

l_y = 6
l_x = 5
counter = 0

for iq, q_x in enumerate([[43,66],[45,34],[4,32],[2,64]]):
    for im in range(4):
        color = 'gray'
        if 'Q{}M{}'.format(iq+1, im+1) in mod_names:
            color = 'green'
        if np.nanmean(constants['Noise'][counter, :, :, :, 0]) == 0:
            color = 'red'
        counter += 1
        x = q_x[0]
        for i_as in range(8):
            ax.add_patch(matplotlib.patches.Rectangle((x,q_x[1]-q_st*im), l_x, l_y, linewidth=2,edgecolor='darkgreen',
                                           facecolor=color, fill=True))
            x += asic_pos
        ax.text(q_x[0]+14.5, q_x[1]-q_st*im+1.5, 'Q{}M{}'.format(
            iq+1, im+1),  fontsize=24, color='gold')

_ = ax.legend(handles=[patches.Patch(facecolor='red', label='No data'),
                       patches.Patch(facecolor='gray', label='Not processed'),
                       patches.Patch(facecolor='green', label='Processed')],
              loc='outside-top', ncol=3, bbox_to_anchor=(0.1, 0.25, 0.7, 0.8))

## Summary figures across Modules ##

The following plots give an overview of calibration constants averaged across pixels and memory cells. A bad pixel mask is applied.

In [ ]:
#Initializing AGIPD geometry
geom = AGIPD_1MGeometry.from_quad_positions(quad_pos=[
        (-525, 625),
        (-550, -10),
        (520, -160),
        (542.5, 475),
    ])
gain_names = ['High-gain', 'Medium-gain', 'Low-gain', 'High-Threshold', 'Medium-Threshold']

Mod_data=OrderedDict()
for const_name, const in constants.items():
    
    if const_name == 'BadPixelsDark':
        continue
    Mod_data[const_name] = OrderedDict()
    Mod_data['prev-{}'.format(const_name)] = OrderedDict()
    display(Markdown('<h3 align="center">{}</h3>'.format(const_name)))
    display(Markdown('<h3 align="center">-------</h3>'.format(const_name)))
    
    for gain in range(5):

        # For high gain than 3, don't pass except for Threshold.
        if const.shape[-1] <= gain:
            continue

        display(Markdown('<h3 align="center">{}</h3>'.format(gain_names[gain])))
        fig, (ax0, ax1) = plt.subplots(ncols=2, figsize=(20, 17.5))
        ax_cbar = fig.add_axes([0.15, 0.2, 0.7, 0.02])  # Create extra axes for the colorbar
        
        for i in range(16):
            qm = "Q{}M{}".format(i//4 + 1, i % 4 + 1)

            values = np.nanmean(const[i, :, :, :, gain], axis=2)
            prev_val = np.nanmean(prev_const[const_name][i, :, :, :, gain], axis=2)
    
            values[values == 0] = np.nan
            prev_val[prev_val == 0] = np.nan
            values = np.moveaxis(values, 0, -1).reshape(1, values.shape[1], values.shape[0])
            prev_val = np.moveaxis(prev_val, 0, -1).reshape(1, prev_val.shape[1], prev_val.shape[0])
            
            try:
               
                Mod_data[const_name][gain_names[gain]] = np.concatenate((Mod_data[const_name][gain_names[gain]],
                                                                         values), axis=0)
        
                Mod_data['prev-{}'.format(const_name)][gain_names[gain]] = \
                            np.concatenate((Mod_data['prev-{}'.format(const_name)][gain_names[gain]],
                                                                         prev_val), axis=0)
            except:                                                        
                Mod_data[const_name][gain_names[gain]] = values
                Mod_data['prev-{}'.format(const_name)][gain_names[gain]] = prev_val

        vmin, vmax = get_range(Mod_data[const_name][gain_names[gain]], 2)
        prev_vmin, prev_vmax = get_range(Mod_data['prev-{}'.format(const_name)][gain_names[gain]], 2)

        geom.plot_data_fast(Mod_data[const_name][gain_names[gain]], vmin=vmin, vmax=vmax,
                             ax=ax0,colorbar={
                        'cax': ax_cbar,
                        'shrink': 0.6,
                        'pad': 0.1,
                        'orientation': 'horizontal'
                    })
        colorbar = ax0.images[0].colorbar
        colorbar.set_label('ADUs')
        geom.plot_data_fast(Mod_data['prev-{}'.format(const_name)][gain_names[gain]], 
                            vmin=prev_vmin, vmax=prev_vmax, ax=ax1,colorbar=False)
        ax0.set_title('{} {}'.format(const_name, gain_names[gain]), fontsize=20)
        ax0.set_xlabel('Columns', fontsize=15)
        ax0.set_ylabel('Rows', fontsize=15)
        ax1.set_title('Previous {} {}'.format(const_name, gain_names[gain]), fontsize=20)
        ax1.set_xlabel('Columns', fontsize=15)
        ax1.set_ylabel('Rows', fontsize=15)
        plt.show()
        

In [ ]:
# Loop over capacitor settings, modules, constants
for const_name, const in constants.items():

    display(Markdown('### Summary across Modules - {}'.format(const_name)))
    for gain in range(3):
        data = np.copy(const[:, :, :, :, gain])
        if const_name != 'BadPixelsDark':
            label = '{} value [ADU], good pixels only'.format(const_name)
            data[constants['BadPixelsDark'][:, :, :, :, gain] > 0] = np.nan
            datamean = np.nanmean(data, axis=(1, 2))

            fig = plt.figure(figsize=(15, 6), tight_layout={
                             'pad': 0.2, 'w_pad': 1.3, 'h_pad': 1.3})
            ax = fig.add_subplot(121)
        else:
            label = 'Fraction of bad pixels'
            data[data > 0] = 1.0
            datamean = np.nanmean(data, axis=(1, 2))
            datamean[datamean == 1.0] = np.nan

            fig = plt.figure(figsize=(15, 6), tight_layout={
                             'pad': 0.2, 'w_pad': 1.3, 'h_pad': 1.3})
            ax = fig.add_subplot(111)

        d = []
        for im, mod in enumerate(datamean):
            d.append({'x': np.arange(mod.shape[0]),
                      'y': mod,
                      'drawstyle': 'steps-pre',
                      'label': mod_names[im],
                      })

        _ = simplePlot(d, figsize=(10, 10), xrange=(-12, 510),
                            x_label='Memory Cell ID',
                            y_label=label,
                            use_axis=ax,
                            title='{} gain'.format(gain_names[gain]),
                            title_position=[0.5, 1.18],
                            legend='outside-top-ncol6-frame', legend_size='18%',
                            legend_pad=0.00)

        if const_name != 'BadPixelsDark':
            ax = fig.add_subplot(122)
            label = '$\sigma$ {} [ADU], good pixels only'.format(const_name)
            d = []
            for im, mod in enumerate(np.nanstd(data, axis=(1, 2))):
                d.append({'x': np.arange(mod.shape[0]),
                          'y': mod,
                          'drawstyle': 'steps-pre',
                          'label': mod_names[im],
                          })

            _ = simplePlot(d, figsize=(10, 10), xrange=(-12, 510),
                                x_label='Memory Cell ID',
                                y_label=label,
                                use_axis=ax,
                                title='{} gain'.format(gain_names[gain]),
                                title_position=[0.5, 1.18],
                                legend='outside-top-ncol6-frame', legend_size='18%',
                                legend_pad=0.00)

        plt.show()

## Summary tables across Modules ##

Tables show values averaged across all pixels and memory cells of a given detector module.

In [ ]:
if u'$' in tabulate.LATEX_ESCAPE_RULES:
    del(tabulate.LATEX_ESCAPE_RULES[u'$'])
    
if u'\\' in tabulate.LATEX_ESCAPE_RULES:
    del(tabulate.LATEX_ESCAPE_RULES[u'\\'])

In [ ]:
header = ['Module', 'High gain', 'Medium gain', 'Low gain']

for const_name, const in constants.items():
    table = []

    for i_mod, mod in enumerate(mod_names):

        t_line = [mod]
        for gain in range(3):
            data = np.copy(const[i_mod, :, :, :, gain])
            if const_name == 'BadPixelsDark':
                data[data > 0] = 1.0
                datasum = np.nansum(data)
                datamean = np.nanmean(data)
                if datamean == 1.0:
                    datamean = np.nan
                    datasum = np.nan

                t_line.append('{:6.0f} ({:6.3f}) '.format(
                    datasum, datamean))

                label = '## Number (fraction) of bad pixels'
            else:

                data[constants['BadPixelsDark']
                     [i_mod, :, :, :, gain] > 0] = np.nan

                t_line.append('{:6.1f} $\\pm$ {:6.1f}'.format(
                    np.nanmean(data), np.nanstd(data)))

                label = '## Average {} [ADU], good pixels only ##'.format(const_name)

        table.append(t_line)

    display(Markdown(label))
    md = display(Latex(tabulate.tabulate(
        table, tablefmt='latex', headers=header)))